In [1]:
from pymongo import MongoClient
import pandas as pd
import folium

client=MongoClient()

db=client.companies

In [2]:
def geoquery(df):            # query geoespacial y criterios de seleccion
    list_money_mean=[]
    sb_ratio=[]
    n_companies=[]
    
    for i in range(len(df)):        # geoquery
        q=list(db.geoloc.find({"geo_loc":{"$near":{"$geometry":{ "type":"Point",
                                                   "coordinates":[df.longitude[i], df.latitude[i]]},
                                                   "$maxDistance":2000}}}))

        l=len(q)
        money_mean=sum([q[j]['n_total_money'] for j in range(l)])/l
        list_money_mean.append(money_mean)             # densidad de dinero
        
        big=sum([q[k]['company_class'].count('Big') if q[k]['company_class'].count('Big')!=0\
                 else 1 for k in range(l)])
        start=sum([q[k]['company_class'].count('StartUp') for k in range(l)])
        sb_ratio.append(start/big)        # ratio startup/big
        
        n_companies.append(l)          # numero de compañias alrededor
        
    df['around_companies']=n_companies    
    df['money_density']=list_money_mean
    df['sb_ratio']=sb_ratio
    
    return df
    

In [3]:
def geomap(df, zoom_start=12):
    
    if len(df)>=15:
        df.index=range(len(df)) 
        
        mapa=folium.Map(location=[float(df.latitude[0]), float(df.longitude[0])],
                    tiles='openstreetmap', zoom_start=zoom_start)
        
        for i in range(1, len(df)):

            folium.CircleMarker([float(df.latitude[i]), float(df.longitude[i])], popup=str(df.name[i]), 
                                 radius=1, icon=folium.Icon()).add_to(mapa)

        mapa.save('geomap.html')
    
    elif len(df)>1 and len(df)<15:
        df.index=range(len(df)) 
        
        mapa=folium.Map(location=[float(df.latitude[0]), float(df.longitude[0])],
                    tiles='openstreetmap', zoom_start=zoom_start)
        
        for i in range(1, len(df)):

            folium.Marker([float(df.latitude[i]), float(df.longitude[i])], popup=str(df.name[i]), 
                                 icon=folium.Icon(color='red')).add_to(mapa)

        mapa.save('geomap.html')
       
    
    else:
        mapa=folium.Map(location=[float(df.latitude), float(df.longitude)],
                    tiles='openstreetmap', zoom_start=zoom_start)
        folium.Marker([float(df.latitude), float(df.longitude)], popup=str(df.name), 
                       icon=folium.Icon(color='red')).add_to(mapa)
        mapa.save('geomap.html')
     
    
    return mapa

In [4]:
if __name__=="__main__":
    
    df=pd.DataFrame(db.geoloc.find())   # carga datos desde mongo
    df=geoquery(df)
    
    print ('Todas las oficinas consideradas.')
    mapa1=geomap(df, zoom_start=1.5)
    display (mapa1)
    
    print ('')
    print ('Compañias alrededor=20, sb_ratio>0.45 y densidad monetaria>1.000.000$ (Paris)')
    mapa2=geomap(df[(df['around_companies']>=20) & (df['sb_ratio']>0.45) & (df['money_density']>1e6)])
    display (mapa2)
    
    print ('')
    print ('Compañias alrededor>=100, sb_ratio>0.25 y densidad monetaria>10.000.000$ (San Francisco)')
    mapa3=geomap(df[(df['around_companies']>=100) & (df['sb_ratio']>0.25) & (df['money_density']>1e7)],
                zoom_start=15)
    display (mapa3)
    
    
    df=df.drop('_id', axis=1)
    df.to_json('geotableau.json', orient='records', lines=True)

Todas las oficinas consideradas.



Compañias alrededor=20, sb_ratio>0.45 y densidad monetaria>1.000.000$ (Paris)



Compañias alrededor>=100, sb_ratio>0.25 y densidad monetaria>10.000.000$ (San Francisco)


In [5]:
#pongo estas lineas despues del main para que se vean los mapas

print ('Todas las oficinas consideradas.')
mapa1=geomap(df, zoom_start=1.5)
mapa1

Todas las oficinas consideradas.


In [6]:
print ('Compañias alrededor=20, sb_ratio>0.45 y densidad monetaria>1.000.000$ (Paris)')
mapa2=geomap(df[(df['around_companies']>=20) & (df['sb_ratio']>0.45) & (df['money_density']>1e6)])
mapa2

Compañias alrededor=20, sb_ratio>0.45 y densidad monetaria>1.000.000$ (Paris)


In [7]:
print ('Compañias alrededor>=100, sb_ratio>0.25 y densidad monetaria>10.000.000$ (San Francisco)')
mapa3=geomap(df[(df['around_companies']>=100) & (df['sb_ratio']>0.25) & (df['money_density']>1e7)],
            zoom_start=15)
mapa3

Compañias alrededor>=100, sb_ratio>0.25 y densidad monetaria>10.000.000$ (San Francisco)
